## 🏀 Multi-Camera Basketball Analysis with VideoDB RTStream

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/video-db/videodb-cookbook/blob/main/real_time_streaming/multicam/Multicam_Basketball_Analysis.ipynb)

*Transforming sports through intelligent AI-powered monitoring*

---

### 🎯 The Challenge: Smart Sports Analytics

Modern sports analysis faces growing challenges in providing real-time insights. From fast-paced plays to subtle player movements, monitoring every aspect of the game is tough.  

**What if AI could monitor all feeds, detect key plays instantly, and generate highlights automatically?**


The Goal → Automate basketball analysis with AI:
- Detect key events in real time  
- Trigger instant alerts for highlights  
- Provide multi-angle replays for analysis


### 🚀 Enter VideoDB RTStream
**VideoDB RTStream** brings AI-powered intelligence to multi-camera sports systems.  
In this demo, a **3-camera basketball setup** can:  
- Monitor the court from multiple angles at once  
- Analyze player actions and game events in real-time  
- Trigger smart alerts for key moments (e.g., basket scored, foul)
- Provide synchronized multi-angle replays for coaches and analysts

### 📊 Dataset: Simulated Live Game Footage

We use **simulated live streams from 3 different camera angles** covering a basketball game.
- **3 cameras**, with overlapping field-of-views
- Each stream captures a unique perspective of the court.

👉 This setup mimics a real-world broadcast or arena setup, perfect for demonstrating multi-camera analysis

Source: West KY Sports Network


### 🎥 What You'll Build

By the end of this notebook, you’ll:  
- Connect & manage **3 synchronized streams** of a basketball game
- Run **AI-powered game analysis** to understand plays
- Set up **intelligent event detection & alerts** for key moments

*This demo shows how AI turns raw game feeds into actionable sports intelligence.*


---
### 📦 Step 1:  Install Dependencies

First, let's install the VideoDB SDK and additional packages needed for multi-camera processing.



In [ ]:
%pip -q install videodb

  Preparing metadata (setup.py) ... done


---
### 🔗 Step 2: Connect to VideoDB

Next, let’s establish a connection to **VideoDB** so we can manage multi-camera streams seamlessly.


In [ ]:
import videodb
import os
from getpass import getpass

api_key = getpass("Please enter your VideoDB API Key: ")

os.environ["VIDEO_DB_API_KEY"] = api_key

conn = videodb.connect()
coll = conn.get_collection()

print("Connected to VideoDB securely!")

Connected to VideoDB securely!


---
### 🎥 Step 3: Configure Multi-Camera Streams

Now we’ll set up the multi-camera system.  
For this demo, we’ll simulate a **🏀 basketball arena** using three camera angles that cover the court.


In [ ]:
# Multi-camera configuration for basketball arena
CAMERA_CONFIG = {
    "setting_name": "🏀 Basketball Arena Monitoring",
    "cameras": {
        "cam1": {
            "name": "Main Court Field",
            "rtsp_url": "rtsp://samples.rts.videodb.io:8554/bb-cam1",
            "position": "Center Court - Wide Angle",
            "description": "Primary court coverage with full court view"
        },
        "cam2": {
            "name": "North Basket Area Field",
            "rtsp_url": "rtsp://samples.rts.videodb.io:8554/bb-cam2",
            "position": "North Basket - Close Up",
            "description": "Focused on north basket area and three-point line"
        },
        "cam3": {
            "name": "South Basket Area Field",
            "rtsp_url": "rtsp://samples.rts.videodb.io:8554/bb-cam3",
            "position": "South Basket - Close Up",
            "description": "Focused on south basket area and paint zone"
        }
    }
}

print(f"🏟️  Setting up: {CAMERA_CONFIG['setting_name']}")
print(f"📹 Camera count: {len(CAMERA_CONFIG['cameras'])}")
print("\n📋 Camera Layout:")
for cam_id, cam_info in CAMERA_CONFIG['cameras'].items():
    print(f"  {cam_id.upper()}: {cam_info['name']} ({cam_info['position']})")


🏟️  Setting up: 🏀 Basketball Arena Monitoring
📹 Camera count: 3

📋 Camera Layout:
  CAM1: Main Court Field (Center Court - Wide Angle)
  CAM2: North Basket Area Field (North Basket - Close Up)
  CAM3: South Basket Area Field (South Basket - Close Up)


---
### 🎯 Step 4: Connect All Camera Streams

Now, let’s connect all **four camera streams** to **VideoDB RTStream** and run them in sync.


*Get all streams*

In [ ]:
# Connect all cameras while reusing existing streams if they already exist
# This avoids creating duplicate RTStream resources.
connected_streams = {}
print("🔌 Connecting to all camera streams (reusing existing where possible)...\n")

# Pre-fetch existing streams once to minimize API calls
try:
    existing_streams = {getattr(s, "name", ""): s for s in coll.list_rtstreams()}
except Exception as e:
    print(f"⚠️  Could not list existing streams: {e}")
    existing_streams = {}

🔌 Connecting to all camera streams (reusing existing where possible)...



*Using existing streams if available*

In [ ]:
for cam_id, cam_info in CAMERA_CONFIG["cameras"].items():
    name = f"{CAMERA_CONFIG['setting_name']} - {cam_info['name']}"
    existing = existing_streams.get(name)

    try:
        if existing:
            print(f"📹 {cam_id.upper()}: Using existing stream '{name}' ({existing.id})")
            if getattr(existing, "status", None) != "connected":
                try:
                    existing.start()
                    print(f"   ▶️ Started existing stream: {existing.id}")
                except Exception as se:
                    print(f"   ⚠️ Could not start existing stream: {se}")
            connected_streams[cam_id] = {"stream": existing, "info": cam_info, "status": "connected"}
        else:
            print(f"📹 {cam_id.upper()}: Creating new stream '{name}'...")
            stream = coll.connect_rtstream(name=name, url=cam_info["rtsp_url"])
            print(f"   ✅ Connected: {stream.id}")
            connected_streams[cam_id] = {"stream": stream, "info": cam_info, "status": "connected"}

    except Exception as e:
        print(f"   ❌ {cam_id.upper()} failed: {e}")
        connected_streams[cam_id] = {"stream": None, "info": cam_info, "status": "failed", "error": str(e)}

# Summary
success = sum(1 for s in connected_streams.values() if s["status"] == "connected")
print(f"\n🎯 Connection Summary: {success}/{len(CAMERA_CONFIG['cameras'])} cameras ready")
print("🚀 Multi-camera system ready for scene indexing!" if success else "⚠️ No cameras ready. Check RTSP URLs/credentials.")


📹 CAM1: Using existing stream '🏀 Basketball Arena Monitoring - Main Court Field' (rts-01993335-5fb5-7420-8020-5f0bcc2e864f)
📹 CAM2: Using existing stream '🏀 Basketball Arena Monitoring - North Basket Area Field' (rts-01993335-606c-7332-8eac-07c580b9569a)
📹 CAM3: Using existing stream '🏀 Basketball Arena Monitoring - South Basket Area Field' (rts-01993335-6147-7601-ab8b-b218bc0ba089)

🎯 Connection Summary: 3/3 cameras ready
🚀 Multi-camera system ready for scene indexing!


#### 🎥 Live Preview of Raw Streams

In [ ]:
import os
from concurrent.futures import ThreadPoolExecutor, as_completed
from IPython.display import Video, display

def connect_and_export_stream(rtsp_url, cam_name, duration=5, output_file="clip.mp4"):
    if os.path.exists(output_file): os.remove(output_file)
    os.system(
        f'ffmpeg -loglevel error -hide_banner -y -rtsp_transport tcp -i "{rtsp_url}" -t {duration} -c copy "{output_file}"'
    )
    if os.path.exists(output_file):
        return cam_name, Video(output_file, embed=True)
    else:
        return cam_name, None

CLIP_DURATION = 10 #Set the Duration here for the clip time

print("🎥 Connecting to all cameras...\n")
futures = []
with ThreadPoolExecutor() as executor:
    for cam_id, cam_info in CAMERA_CONFIG["cameras"].items():
        out_file = f"{cam_id}_clip.mp4"
        futures.append(
            executor.submit(connect_and_export_stream, cam_info["rtsp_url"], cam_info["name"], CLIP_DURATION, out_file)
        )

    for future in as_completed(futures):
        cam_name, clip = future.result()
        if clip:
            print(f"✅ {cam_name} ready:")
            display(clip)
        else:
            print(f"❌ Failed to capture {cam_name}")


🎥 Connecting to all cameras...

✅ Main Court Field ready:


✅ North Basket Area Field ready:


✅ South Basket Area Field ready:


---
### 🗂️ Step 5: Set Up Scene Indexing

Now we’ll build **scene indexes** for each camera stream, enabling AI-powered analysis across all viewpoints.


*a. Index Config*

In [ ]:
from videodb import SceneExtractionType

# Scene indexing configuration
SCENE_INDEX_CONFIG = {
    "extraction_type": SceneExtractionType.time_based,
    "extraction_config": {
        "time": 15,  # Analyze every 15 seconds
        "frame_count": 1
    },
    "prompt": """Analyze this basketball game footage and describe:
    1. Player positions and movements on the court
    2. Ball location and which team has possession
    3. Any significant events (baskets scored, fouls, free throws, timeouts)
    4. Defensive and offensive plays being executed
    5. Crowd reactions or unusual activities
    6. Any safety or security concerns

    Be specific about what you observe in this camera angle."""
}

*b. Setup Index*

In [ ]:
# 🔍 List existing scene indexes for connected cameras
for cam_id, cam_data in connected_streams.items():
    if cam_data["status"] != "connected":
        print(f"⏭️ {cam_id.upper()}: Stream not connected")
        continue

    try:
        indexes = cam_data["stream"].list_scene_indexes()
        if indexes:
            print(f"📑 {cam_id.upper()} ({cam_data['info']['name']}):")
            for idx in indexes:
                print(f"   • {idx.name} (ID: {idx.rtstream_index_id}, Status: {getattr(idx, 'status', 'unknown')})")
        else:
            print(f"📑 {cam_id.upper()}: No indexes found")
    except Exception as e:
        print(f"⚠️ {cam_id.upper()}: Failed to list indexes ({e})")

📑 CAM1: No indexes found
📑 CAM2: No indexes found
📑 CAM3: No indexes found


In [ ]:
# ⚙️ Setup or reuse scene indexes
scene_indexes = {}
print("🔧 Setting up scene indexes...\n")

for cam_id, cam_data in connected_streams.items():
    if cam_data["status"] != "connected":
        continue

    stream = cam_data["stream"]
    name = f"Basketball_Arena_{cam_id.upper()}_Index"

    try:
        # Check if an index with this name exists
        existing = next((idx for idx in stream.list_scene_indexes() if getattr(idx, "name", "") == name), None)

        if existing:
            print(f"📊 {cam_id.upper()}: Using existing index '{name}' ({existing.rtstream_index_id})")
            if getattr(existing, "status", None) not in ("running", "active", "connected"):
                try:
                    existing.start()
                    print(f"   ▶️ Started index: {existing.rtstream_index_id}")
                except Exception as se:
                    print(f"   ⚠️ Could not start index: {se}")
            scene_indexes[cam_id] = {"index": existing, "index_id": existing.rtstream_index_id, "status": "active"}
        else:
            print(f"📊 {cam_id.upper()}: Creating new index '{name}'...")
            new_idx = stream.index_scenes(
                extraction_type=SCENE_INDEX_CONFIG["extraction_type"],
                extraction_config=SCENE_INDEX_CONFIG["extraction_config"],
                prompt=SCENE_INDEX_CONFIG["prompt"],
                name=name,
            )
            scene_indexes[cam_id] = {"index": new_idx, "index_id": new_idx.rtstream_index_id, "status": "active"}
            print(f"   ✅ Index created: {new_idx.rtstream_index_id}")

    except Exception as e:
        print(f"❌ {cam_id.upper()}: Failed to setup index ({e})")
        scene_indexes[cam_id] = {"index": None, "index_id": None, "status": "failed", "error": str(e)}

# Summary
active = sum(1 for idx in scene_indexes.values() if idx["status"] == "active")
print(f"\n🎯 Scene Indexing Summary: {active}/{len(connected_streams)} active")
print("🔍 AI analysis running (every 15s)" if active else "⚠️ No indexes active. Check streams and retry.")

🔧 Setting up scene indexes...

📊 CAM1: Creating new index 'Basketball_Arena_CAM1_Index'...
   ✅ Index created: aacf53d17fa9d846
📊 CAM2: Creating new index 'Basketball_Arena_CAM2_Index'...
   ✅ Index created: b316da9dae1a03fb
📊 CAM3: Creating new index 'Basketball_Arena_CAM3_Index'...
   ✅ Index created: 05af0ba36e399502

🎯 Scene Indexing Summary: 3/3 active
🔍 AI analysis running (every 15s)


---
## 🚨 Phase 2: Set and Receive Alerts

In this phase, we’ll configure alert rules and handle incoming alerts from the multi-camera streams.

### ⚙️ Step 1: Configure and setup events

*Alert Config & Events*

In [ ]:
# 🏀 Define basketball arena events
EVENTS_CONFIG = [
    {"label": "basket scored", "prompt": "Detect when a basket is scored (ball through hoop, celebrations, or score change).", "description": "Basket scored"},
    {"label": "player foul", "prompt": "Detect fouls, aggressive behavior, or rule violations.", "description": "Player foul or violation"},
    {"label": "timeout called", "prompt": "Detect when a timeout is called (players huddle or referee signals).", "description": "Timeout called"},
]

# 🔍 List existing events in VideoDB
existing_events_by_label = {}
try:
    for evt in conn.list_events():
        lbl = evt["label"]
        eid = evt["event_id"]
        if lbl and eid:
            existing_events_by_label[lbl] = eid
    if existing_events_by_label:
        print("📑 Existing events found:")
        for lbl, eid in existing_events_by_label.items():
            print(f"   • {lbl} ({eid})")
    else:
        print("📑 No existing events found.")
except Exception as e:
    print(f"⚠️ Could not list existing events: {e}")


📑 Existing events found:
   • timeout_called (0bb5f68981208827)
   • person_with_trolley (0c9831d3a5d702b3)
   • large_crowd_formation (1a5585203e9374d1)
   • suspicious_loitering (3307388de055afbe)
   • basket scored (49977929774f8cd7)
   • player foul (53409a9e89f66846)
   • basket_scored (6c08568f54b59644)
   • unattended_luggage (87a452a83bc362ad)
   • timeout called (902fdd5571bacf30)
   • woman_in_red_coat (afe2776cf3f4608c)
   • player_foul (cab9b3430d908e31)


In [ ]:
# 🚀 Create or reuse events in VideoDB
created_events = {}
print("\n🎯 Setting up cross-camera event detection...\n")

for cfg in EVENTS_CONFIG:
    label = cfg["label"]

    if label in existing_events_by_label:
        event_id = existing_events_by_label[label]
        created_events[label] = {"event_id": event_id, "config": cfg, "status": "existing"}
        print(f"📎 Using existing event: {label} ({event_id})")
        continue

    try:
        print(f"📝 Creating event: {label}...")
        event_id = conn.create_event(event_prompt=cfg["prompt"], label=label)
        created_events[label] = {"event_id": event_id, "config": cfg, "status": "created"}
        print(f"   ✅ Created: {event_id}")
    except Exception as e:
        print(f"   ❌ Failed: {e}")
        created_events[label] = {"event_id": None, "config": cfg, "status": "failed", "error": str(e)}

# 📊 Summary
created = sum(1 for e in created_events.values() if e["status"] == "created")
existing = sum(1 for e in created_events.values() if e["status"] == "existing")
print(f"\n🎯 Events ready: {existing} existing, {created} created ({existing+created}/{len(EVENTS_CONFIG)})")

if existing + created:
    print("🚀 Event detection system ready! Monitoring for:")
    for lbl, evt in created_events.items():
        if evt["status"] in ("created", "existing"):
            print(f"   • {lbl}: {evt['config']['description']}")
else:
    print("⚠️ No events ready. Check configuration and retry.")



🎯 Setting up cross-camera event detection...

📎 Using existing event: basket scored (49977929774f8cd7)
📎 Using existing event: player foul (53409a9e89f66846)
📎 Using existing event: timeout called (902fdd5571bacf30)

🎯 Events ready: 3 existing, 0 created (3/3)
🚀 Event detection system ready! Monitoring for:
   • basket scored: Basket scored
   • player foul: Player foul or violation
   • timeout called: Timeout called


---
### 🌐 Step 2: Configure Webhook & Callback

*a. install pyngrok*

In [ ]:
!pip install pyngrok
!pip install flask

*b. Expose a Public Webhook URL (ngrok or fallback)*

> ⚡ **Note:**  
> - **Local setup**: You can comment out these lines and just pass an empty string for the token:  
>   ```python
>   # from google.colab import userdata
>   # token = userdata.get('ngrok_auth')
>   token = ""
>   ```
>
> - **Google Colab**: Create a secret and fetch it using `userdata`.  
>   You can generate your Ngrok **Auth Token** here: [Ngrok Dashboard](https://dashboard.ngrok.com/get-started/your-authtoken)


In [ ]:
import os
import socket
from pyngrok import ngrok
from google.colab import userdata

def choose_port(start=5001, tries=5):
    """Pick an available local port (default: 5001–5005)."""
    for p in range(start, start + tries):
        with socket.socket(socket.AF_INET, socket.SOCK_STREAM) as s:
            try:
                s.bind(("0.0.0.0", p))
                return p
            except OSError:
                continue
    return start

try:
    # Authenticate ngrok if token available
    token = userdata.get('ngrok_auth')
    if token:
        ngrok.set_auth_token(token)

    WEBHOOK_PORT = choose_port()
    tunnel = ngrok.connect(WEBHOOK_PORT)
    PUBLIC_WEBHOOK_URL = f"{tunnel.public_url}/webhook"
    print(f"🌍 Public webhook URL: {PUBLIC_WEBHOOK_URL}")
except Exception as e:
    PUBLIC_WEBHOOK_URL = ""
    print(f"⚠️ ngrok tunnel not started: {e}")
    print("➡️  Set `WEBHOOK_URL` manually if using external service (Zapier, Pipedream, etc.).")

# Unified callback (used when creating alerts)
ALERT_CALLBACK_URL = PUBLIC_WEBHOOK_URL or ""
if ALERT_CALLBACK_URL:
    print(f"✅ Callback URL configured: {ALERT_CALLBACK_URL}")
else:
    print("⚠️ No callback URL configured — alerts won’t trigger notifications.")


🌍 Public webhook URL: https://aec9b708aa90.ngrok-free.app/webhook
✅ Callback URL configured: https://aec9b708aa90.ngrok-free.app/webhook


*c. Webhook Receiver (Flask server)*

In [ ]:
import time
import threading
from flask import Flask, request, jsonify

# In-memory store for webhook calls
webhook_data = globals().get("webhook_data", [])
webhook_meta = globals().get("webhook_meta", {"started_at": time.time(), "count": 0})

app = Flask(__name__)

@app.route("/webhook", methods=["POST"])
def webhook():
    payload = request.get_json(silent=True) or {}
    webhook_meta["count"] += 1
    webhook_data.append({
        "received_at": time.time(),
        "headers": dict(request.headers),
        "data": payload
    })
    webhook_data[:] = webhook_data[-500:]  # keep last 500 only
    print(f"📩 Webhook #{webhook_meta['count']} received: {payload}")
    return jsonify({"status": "ok"})

def run_webhook():
    app.run(host="0.0.0.0", port=WEBHOOK_PORT, debug=False, use_reloader=False)

# Start/reuse thread safely
webhook_thread = globals().get("webhook_thread")
if not webhook_thread or not webhook_thread.is_alive():
  webhook_thread = threading.Thread(target=run_webhook, daemon=True)
  webhook_thread.start()
  globals()["webhook_thread"] = webhook_thread
  print(f"🚀 Webhook server running at http://localhost:{WEBHOOK_PORT}/webhook")
else:
    print(f"✅ Webhook server already running at http://localhost:{WEBHOOK_PORT}/webhook")


🚀 Webhook server running at http://localhost:5001/webhook


---
### 🚨 Step 3: Multi-Camera Alert System

We’ll now set up an **intelligent alerting pipeline** that continuously monitors all connected cameras.  
Whenever a basketball event is detected, the system will trigger a **real-time notification** enriched with **multi-angle evidence clips** for better context.

*a. Callback & Setup*

In [ ]:
# 🚨 Step 3A: Prepare callback + alert storage

# Use callback URL from earlier cells
callback_url = globals().get("ALERT_CALLBACK_URL", "")
if not callback_url:
    print("⚠️ No callback URL configured. Alerts will be created but won't send notifications.")

# Container for alerts per camera
created_alerts = {}
print("🚨 Setting up alerts (reuse existing where possible)\n")


🚨 Setting up alerts (reuse existing where possible)



*b. Create or Reuse Alerts*

In [ ]:
for cam_id, idx_data in scene_indexes.items():
    if idx_data.get("status") != "active" or not idx_data.get("index"):
        print(f"⏭️ {cam_id.upper()}: Index not active → skipping alerts")
        continue

    idx = idx_data["index"]
    cam_name = connected_streams[cam_id]["info"]["name"]
    created_alerts[cam_id] = {}

    # Try to list existing alerts for this index
    existing_alerts = {}
    try:
        for a in idx.list_alerts():
            label = a["label"]
            aid = a["alert_id"]
            if label and aid:
                existing_alerts[label] = a
    except Exception as e:
        print(f"   ⚠️ {cam_id.upper()}: Could not list existing alerts: {e}")

    print(f"📹 {cam_id.upper()}: {cam_name}")

    # For each defined event → create/reuse alerts
    for label, evt in created_events.items():
        if evt.get("status") not in ("existing", "created") or not evt.get("event_id"):
            continue

        if label in existing_alerts and callback_url == a["callback_url"]:
            if a["status"] == "disabled":
                idx.enable_alert(a["alert_id"])
            a = existing_alerts[label]
            aid = a["alert_id"]
            created_alerts[cam_id][label] = {"alert_id": aid, "event_id": evt["event_id"], "status": "existing"}
            print(f"   📎 Using existing alert for '{label}': {aid}")

        else:
            try:
                aid = idx.create_alert(evt["event_id"], callback_url=callback_url or None)
                status = "active" if callback_url else "created_no_webhook"
                created_alerts[cam_id][label] = {"alert_id": aid, "event_id": evt["event_id"], "status": status}
                msg = f"   ✅ Created alert for '{label}': {aid}" if callback_url else f"   ⚠️ Created alert for '{label}' (no webhook)"
                print(msg)
            except Exception as e:
                created_alerts[cam_id][label] = {"alert_id": None, "event_id": evt["event_id"], "status": "failed", "error": str(e)}
                print(f"   ❌ Failed to create alert for '{label}': {e}")

📹 CAM1: Main Court Field
   ✅ Created alert for 'basket scored': 18fe0dd6048b208f
   ✅ Created alert for 'player foul': c5bcd7843e27ece1
   ✅ Created alert for 'timeout called': 8be09efe80b15a56
📹 CAM2: North Basket Area Field
   ✅ Created alert for 'basket scored': 1620495094e55fc0
   ✅ Created alert for 'player foul': 3fe89f697c326590
   ✅ Created alert for 'timeout called': 0f741dd9bb46e5ea
📹 CAM3: South Basket Area Field
   ✅ Created alert for 'basket scored': af945e9619670c13
   ✅ Created alert for 'player foul': 01cde5c09603ce70
   ✅ Created alert for 'timeout called': 13f33c5b073a9b64


In [ ]:
# 📊 Alert system summary
num_total = sum(len(alerts) for alerts in created_alerts.values())
num_ready = sum(
    1 for cam_alerts in created_alerts.values()
    for a in cam_alerts.values()
    if a["status"] in ("active", "existing", "created_no_webhook")
)

print(f"\n🎯 Alert System Summary: {num_ready}/{num_total} alerts ready")
if num_ready:
    print(f"📬 Alerts will POST to: {callback_url or '❌ (no webhook set)'}")
else:
    print("⚠️ No alerts ready. Check indexes, events, and callback URL.")



🎯 Alert System Summary: 9/9 alerts ready
📬 Alerts will POST to: https://aec9b708aa90.ngrok-free.app/webhook


---
## 📡 Phase 3: Alerts & Data Processing

With alerts now streaming in from all cameras, this phase focuses on **capturing, processing, and analyzing** those incoming events.  
We’ll store webhook data in-memory, extract useful context, and prepare it for downstream workflows like dashboards, notifications, or automated actions.

In [ ]:
len(webhook_data)

24

In [ ]:
webhook_data[:1]

[{'received_at': 1757503276.671652,
  'headers': {'Host': 'aec9b708aa90.ngrok-free.app',
   'User-Agent': 'Python/3.12 aiohttp/3.11.11',
   'Content-Length': '787',
   'Accept': '*/*',
   'Accept-Encoding': 'gzip, deflate',
   'Content-Type': 'application/json',
   'X-Forwarded-For': '54.205.49.109',
   'X-Forwarded-Host': 'aec9b708aa90.ngrok-free.app',
   'X-Forwarded-Proto': 'https'},
  'data': {'event_id': 'event-49977929774f8cd7',
   'label': 'basket scored',
   'confidence': 0.95,
   'explanation': 'The ball is depicted directly above the rim and net, appearing to descend through the hoop, strongly indicating a basket is being scored.',
   'timestamp': '2025-09-10T11:21:16.614553+00:00',
   'start_time': '2025-09-10T16:50:45.698108+05:30',
   'end_time': '2025-09-10T16:51:00.698108+05:30',
   'stream_url': 'https://videodb-rt-streaming-service-us-east-1.s3.us-east-1.amazonaws.com/manifests/rts-01993335-5fb5-7420-8020-5f0bcc2e864f/1757503245000000-1757503261000000.m3u8',
   'player

---
### 🎯 Step 1: Choose the Event

From the list of recent alerts, select a specific **basketball event** you’d like to explore further.  
This choice will be used to extract the event window (with multiple camera angles) for deeper analysis.


In [ ]:
# 📡 View & select recent alerts (last 10)

# Keep only the last 10 webhook events
recent_alerts = webhook_data[-10:] if webhook_data else []

if not recent_alerts:
    print("⚠️ No alerts received yet.")
else:
    # Normalize alerts into a compact list
    cleaned_alerts = []
    for item in recent_alerts:
        data = item.get("data", {})
        cleaned_alerts.append({
            "label": data.get("label", "N/A"),
            "confidence": data.get("confidence", "N/A"),
            "explanation": (data.get("explanation") or "")[:100]+"...",
            "timestamp": data.get("timestamp", "N/A"),
            "start_time": data.get("start_time", "N/A"),
            "end_time": data.get("end_time", "N/A"),
            "stream_url": data.get("stream_url", "N/A"),
            "player_url": data.get("player_url", "N/A"),
            "event_id": data.get("event_id", "N/A"),
        })

    # Display to user
    print("\n📋 Recent Alerts (last 10):\n")
    for i, alert in enumerate(cleaned_alerts, 1):
        print(f"{i}. 🎯 {alert['label']} | "
              f"✅ {alert['confidence']} | 📝 {alert['explanation']}")

    # Interactive selection
    try:
        choice = int(input("\n👉 Select an alert (1–{0}): ".format(len(cleaned_alerts))).strip())
        if 1 <= choice <= len(cleaned_alerts):
            selected = cleaned_alerts[choice - 1]
            print(f"\n✅ Selected: {selected['label']} "
                  f"(Confidence: {selected['confidence']})")
        else:
            print("⚠️ Invalid selection. Please choose a valid alert number.")
    except (ValueError, EOFError):
        print("⚠️ No valid input received. Skipping selection.")



📋 Recent Alerts (last 10):

1. 🎯 basket scored | ✅ 0.95 | 📝 The ball is depicted directly above the rim and net, appearing to descend through the hoop, strongly...
2. 🎯 player foul | ✅ 0.9 | 📝 An alert is triggered because the scene analysis indicates a potential foul. Maroon player #1 is in ...
3. 🎯 timeout called | ✅ 0.9 | 📝 Players in dark jerseys are clustered together in what appears to be a huddle, and the overall still...

👉 Select an alert (1–3): 1

✅ Selected: basket scored (Confidence: 0.95)


---
###  🎥 Step 2: Retrieve Multi-Camera Feeds for the Same Timestamp

Once an event is selected, we’ll fetch the **synchronized video segments** from all connected cameras.  
This ensures you get a **multi-angle replay** of the same moment in time, making analysis more accurate and contextual.

*a. Parse the timeline*

In [ ]:
import re
from datetime import datetime, timezone

# ⚙️ Config: symmetric padding around the alert window
OFFSET_SECONDS = 10

# 🔎 Regex to extract timestamps from HLS stream URLs
_STREAM_RE = re.compile(r"/(\d{16})-(\d{16})\.m3u8")

def parse_stream_times(url: str):
    """Extract start/end timestamps (in seconds) from stream URL."""
    if not url:
        return None, None
    match = _STREAM_RE.search(url)
    if not match:
        return None, None
    return int(match[1]) / 1e6, int(match[2]) / 1e6

def parse_iso_ts(ts: str):
    """Convert ISO timestamp string to epoch seconds."""
    if not ts:
        return None
    dt = datetime.fromisoformat(ts)
    if dt.tzinfo is None:
        dt = dt.replace(tzinfo=timezone.utc)
    return int(dt.timestamp())

# 📦 Extract payload from selection
if not selected:
    raise RuntimeError("❌ No event data found in webhook payload.")

label       = selected.get("label", "unknown")
confidence  = selected.get("confidence", "N/A")
explanation = selected.get("explanation", "")
stream_url  = selected.get("stream_url", "")
player_url  = selected.get("player_url", "")
event_id    = selected.get("event_id", "")
timestamp   = selected.get("timestamp", "")

# 🕒 Resolve event time window
start_s, end_s = parse_stream_times(stream_url)

if not (start_s and end_s):
    start_s = parse_iso_ts(selected.get("start_time"))
    end_s   = parse_iso_ts(selected.get("end_time"))

if not (start_s and end_s):
    raise RuntimeError("❌ Could not determine alert time window from payload.")

# Apply symmetric offset
start_adj = max(0, int(start_s) - OFFSET_SECONDS)
end_adj   = int(end_s) + OFFSET_SECONDS

print(f"⏱️ Time window: {start_adj} → {end_adj} (with ±{OFFSET_SECONDS}s padding)")


⏱️ Time window: 1757503235 → 1757503271 (with ±10s padding)


*b. Generating all streams*

In [ ]:
# Display alert details
print("\n" + "="*70)
print(f"🚨 PROCESSING ALERT: {label.upper()}")
print("="*70)
print(f"📊 Confidence: {confidence}")
print(f"🆔 Event ID: {event_id}")
print(f"⏰ Detected at: {timestamp}")
# print(f"📝 Explanation: {explanation}")
# print(f"\n🕐 TIME WINDOW:")
# print(f"   Original: {datetime.utcfromtimestamp(int(start_s))} → {datetime.utcfromtimestamp(int(end_s))} UTC")
# print(f"   With ±{OFFSET_SECONDS}s: {datetime.utcfromtimestamp(start_adj)} → {datetime.utcfromtimestamp(end_adj)} UTC")
print(f"\n🎥 Original Alert Stream: {player_url or stream_url}")

# Generate synchronized streams for all connected cameras
if not globals().get("connected_streams"):
    raise RuntimeError("connected_streams not found. Run the connection step first.")



🚨 PROCESSING ALERT: BASKET SCORED
📊 Confidence: 0.95
🆔 Event ID: event-49977929774f8cd7
⏰ Detected at: 2025-09-10T11:21:16.614553+00:00

🎥 Original Alert Stream: https://console.videodb.io/player?url=https://videodb-rt-streaming-service-us-east-1.s3.us-east-1.amazonaws.com/manifests/rts-01993335-5fb5-7420-8020-5f0bcc2e864f/1757503245000000-1757503261000000.m3u8


In [ ]:
from videodb import play_stream

multi_camera_streams = {}
print("\n📹 MULTI-CAMERA SYNCHRONIZED STREAMS:")
print("-"*70)

for cam_id, cam_data in connected_streams.items():
    if cam_data.get("status") != "connected" or not cam_data.get("stream"):
        print(f"⏭️ {cam_id.upper()} - {cam_data['info']['name']}: Not connected")
        continue

    try:
        url = cam_data["stream"].generate_stream(start_adj, end_adj)
        player = play_stream(url)
        multi_camera_streams[cam_id] = {
            "camera_name": cam_data["info"]["name"],
            "stream_url": url,
            "player_url": player,
        }
        print(f"✅ {cam_id.upper()} - {cam_data['info']['name']}:")
        # print(f"   📺 {player}")

    except Exception as e:
        print(f"❌ {cam_id.upper()} - {cam_data['info']['name']}: Failed ({e})")

print(f"\n🎯 SUMMARY: Generated {len(multi_camera_streams)} synchronized camera streams")
# print("💡 Use 'multi_camera_streams' dict for multi-view rendering or timeline composition")

camera_feeds = [ feed["player_url"] for feed in multi_camera_streams.values() ]


📹 MULTI-CAMERA SYNCHRONIZED STREAMS:
----------------------------------------------------------------------
✅ CAM1 - Main Court Field:
✅ CAM2 - North Basket Area Field:
✅ CAM3 - South Basket Area Field:

🎯 SUMMARY: Generated 3 synchronized camera streams


In [ ]:
camera_feeds[1]

#### 🧹 Finally: Clean Up Resources

In [ ]:
# Confirm before stopping all streams
active_streams = [s for s in connected_streams.values() if s.get("status") == "connected" and s.get("stream")]
if not active_streams:
    print("✅ All streams are already disconnected.")
else:
    try:
        confirm = input(f"❓ Stop all {len(active_streams)} active streams? (y/n): ").strip().lower()
        if confirm == 'y':
            print("\n🔌 Disconnecting all streams...")
            for cam_data in active_streams:
                try:
                    cam_data["stream"].stop()
                    cam_name = cam_data["info"]["name"]
                    print(f"   ✅ Stopped stream: {cam_name}")
                except Exception as e:
                    print(f"   ❌ Failed to stop stream {cam_name}: {e}")
            print("\n🧹 All streams have been disconnected.")
        else:
            print("\n👍 Streams will remain active.")
    except (ValueError, EOFError):
        print("\n⚠️ No valid input received. Streams will remain active.")

❓ Stop all 3 active streams? (y/n): y

🔌 Disconnecting all streams...
   ✅ Stopped stream: Main Court Field
   ✅ Stopped stream: North Basket Area Field
   ✅ Stopped stream: South Basket Area Field

🧹 All streams have been disconnected.
